In [2]:
#  Copyright 2016 The TensorFlow Authors. All Rights Reserved.
#
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#
#   http://www.apache.org/licenses/LICENSE-2.0
#
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.
"""Convolutional Neural Network Estimator for MNIST, built with tf.layers."""

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    # Reshape X to 4-D tensor: [batch_size, width, height, channels]
    # MNIST images are 28x28 pixels, and have one color channel
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional Layer #1
    # Computes 32 features using a 5x5 filter with ReLU activation.
    # Padding is added to preserve width and height.
    # Input Tensor Shape: [batch_size, 28, 28, 1]
    # Output Tensor Shape: [batch_size, 28, 28, 32]
    conv1 = tf.layers.conv2d(
        inputs=input_layer,
        filters=32,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # Pooling Layer #1
    # First max pooling layer with a 2x2 filter and stride of 2
    # Input Tensor Shape: [batch_size, 28, 28, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 32]
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Convolutional Layer #2
    # Computes 64 features using a 5x5 filter.
    # Padding is added to preserve width and height.
    # Input Tensor Shape: [batch_size, 14, 14, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 64]
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # Pooling Layer #2
    # Second max pooling layer with a 2x2 filter and stride of 2
    # Input Tensor Shape: [batch_size, 14, 14, 64]
    # Output Tensor Shape: [batch_size, 7, 7, 64]
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Flatten tensor into a batch of vectors
    # Input Tensor Shape: [batch_size, 7, 7, 64]
    # Output Tensor Shape: [batch_size, 7 * 7 * 64]
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

    # Dense Layer
    # Densely connected layer with 1024 neurons
    # Input Tensor Shape: [batch_size, 7 * 7 * 64]
    # Output Tensor Shape: [batch_size, 1024]
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

    # Add dropout operation; 0.6 probability that element will be kept
    dropout = tf.layers.dropout(
        inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits layer
    # Input Tensor Shape: [batch_size, 1024]
    # Output Tensor Shape: [batch_size, 10]
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
        # Generate predictions (for PREDICT and EVAL mode)
        "classes": tf.argmax(input=logits, axis=1),
        # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
        # `logging_hook`.
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
            labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
        mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
    # Load training and eval data
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images  # Returns np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images  # Returns np.array
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

    # Create the Estimator
    mnist_classifier = tf.estimator.Estimator(
        model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

    # Set up logging for predictions
    # Log the values in the "Softmax" tensor with label "probabilities"
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(
        tensors=tensors_to_log, every_n_iter=50)

    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": train_data},
        y=train_labels,
        batch_size=100,
        num_epochs=None,
        shuffle=True)
    mnist_classifier.train(
        input_fn=train_input_fn,
        steps=20000,
        hooks=[logging_hook])

    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": eval_data},
        y=eval_labels,
        num_epochs=1,
        shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)


if __name__ == "__main__":
    tf.app.run()

/usr/local/lib/python3.5/dist-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_task_type': 'worker', '_log_step_count_steps': 100, '_task_id': 0, '_save_summary_steps': 100, '_keep_checkpoint_every_n_hours': 10000, '_global_id_in_cluster': 0, '_evaluation_master': '', '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7efe11db73c8>, '_num_worker_replicas': 1, '_master': '', '_session_config': None, '_model_dir': '/tmp/mnist_convnet_model', '_num_ps_replicas': 0, '_keep_checkpoint_max': 5, '_save_checkpoints_secs': 600, '_tf_random_seed': None, '_service': None, '_save_checkpoints_steps': None}
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensor

INFO:tensorflow:step = 1, loss = 2.298772
INFO:tensorflow:probabilities = [[0.09649975 0.09055507 0.0942692  0.10729945 0.11063758 0.09946155
  0.09664271 0.10368602 0.10525101 0.09569764]
 [0.09269538 0.09626238 0.10060668 0.09669323 0.10125039 0.11415356
  0.10080288 0.1111601  0.09377101 0.09260448]
 [0.10421174 0.0915043  0.10240551 0.0984958  0.10044558 0.10134029
  0.09531824 0.1052264  0.09606799 0.1049842 ]
 [0.09567914 0.10107704 0.09297213 0.10701972 0.10277657 0.094075
  0.09315915 0.11067817 0.10698378 0.09557933]
 [0.09415384 0.09850047 0.09860341 0.09712891 0.09722629 0.10909464
  0.09516419 0.10928973 0.10651629 0.09432216]
 [0.09613033 0.09561865 0.1045922  0.09785918 0.10927773 0.10627877
  0.08880506 0.10931796 0.09147198 0.10064814]
 [0.09914339 0.09549627 0.09312487 0.10212292 0.09030997 0.10523979
  0.09949379 0.1338416  0.09722412 0.08400327]
 [0.09792894 0.09530317 0.11404157 0.09005252 0.10014382 0.11213863
  0.08837716 0.1032403  0.10282914 0.09594475]
 [0.0949

INFO:tensorflow:global_step/sec: 155.578
INFO:tensorflow:probabilities = [[0.10548605 0.09509728 0.10739283 0.10202432 0.09584948 0.10201674
  0.09647003 0.09279944 0.10165203 0.10121182]
 [0.09430694 0.0895395  0.10090388 0.10082666 0.100671   0.10673691
  0.10085932 0.10530972 0.10207577 0.09877036]
 [0.10601678 0.09803467 0.0918097  0.09586006 0.09449118 0.11152978
  0.0995239  0.0981747  0.10700636 0.09755283]
 [0.10170054 0.10117951 0.09654956 0.08940274 0.10706419 0.11263482
  0.09973028 0.09998025 0.10013103 0.09162712]
 [0.1030109  0.09242482 0.10266742 0.10321089 0.09245997 0.10340635
  0.09190764 0.105932   0.10233425 0.10264578]
 [0.10678802 0.10001868 0.09413052 0.09883691 0.10805776 0.10779628
  0.09455156 0.09609611 0.09396817 0.099756  ]
 [0.10027327 0.09711486 0.10516543 0.10444502 0.10064863 0.09722197
  0.09230336 0.10506368 0.10182001 0.09594376]
 [0.10009763 0.09337002 0.0994567  0.10736068 0.10199928 0.10473146
  0.08572766 0.1001544  0.09437387 0.1127283 ]
 [0.091

INFO:tensorflow:step = 101, loss = 2.2834437 (0.643 sec)
INFO:tensorflow:probabilities = [[0.09754051 0.10039206 0.09253088 0.10973581 0.11065863 0.08995054
  0.09777726 0.09837504 0.08914184 0.11389747]
 [0.09374313 0.1022432  0.09285831 0.10216533 0.09885306 0.10121615
  0.1035568  0.09851477 0.10516074 0.10168847]
 [0.09054881 0.0974678  0.10770579 0.11171187 0.09821827 0.1124462
  0.09176093 0.09865529 0.08888593 0.10259917]
 [0.09675737 0.1010154  0.09283808 0.09709763 0.1076583  0.10343618
  0.09756573 0.09812424 0.09965321 0.10585393]
 [0.10022258 0.08667326 0.09732876 0.09732256 0.10037758 0.10370028
  0.09813454 0.11641771 0.0982675  0.10155521]
 [0.1010216  0.10108218 0.09717349 0.10236557 0.09935388 0.10138962
  0.09768846 0.10502504 0.09488343 0.10001678]
 [0.08944561 0.09585545 0.10391772 0.09629834 0.11033399 0.10159033
  0.10405874 0.09824802 0.10101739 0.09923449]
 [0.09745382 0.0993814  0.10004608 0.09823804 0.10353885 0.10117744
  0.09090221 0.10367486 0.10859525 0.09

...

INFO:tensorflow:global_step/sec: 201.372
INFO:tensorflow:probabilities = [[0.00003879 0.00819827 0.00204919 0.04535292 0.6995821  0.00260709
  0.00084913 0.0008768  0.01240067 0.22804505]
 [0.00000354 0.9977984  0.00006604 0.00011082 0.00009899 0.00000117
  0.00000752 0.00180867 0.00005727 0.0000475 ]
 [0.         0.         0.00000021 0.0000017  0.99182    0.00000003
  0.00000008 0.00001691 0.00001332 0.00814777]
 [0.00000003 0.0000972  0.00106042 0.99868983 0.00000001 0.00002235
  0.00000001 0.00003894 0.00009029 0.0000009 ]
 [0.00220272 0.00065466 0.02145969 0.00191742 0.00586925 0.01728128
  0.0504428  0.00007913 0.89890194 0.00119107]
 [0.9999572  0.00000001 0.00000902 0.00000196 0.00000005 0.00000016
  0.0000308  0.00000034 0.00000039 0.00000005]
 [0.00112387 0.00000988 0.00012407 0.00000293 0.00007326 0.00006038
  0.99826413 0.00000103 0.00005818 0.00028233]
 [0.00014887 0.99005985 0.00032747 0.00040803 0.00015647 0.00019376
  0.00071272 0.00039224 0.00757433 0.00002616]
 [0.000

INFO:tensorflow:step = 19901, loss = 0.13370913 (0.495 sec)
INFO:tensorflow:probabilities = [[0.00011708 0.00037441 0.00038829 0.05594814 0.00004186 0.87471145
  0.0000723  0.00083804 0.01382912 0.05367934]
 [0.00001913 0.9963075  0.00009966 0.00111589 0.00008978 0.00023804
  0.00011737 0.00076601 0.00078658 0.00045997]
 [0.00047106 0.00000096 0.00000039 0.0000076  0.00011274 0.00012954
  0.00000004 0.99659246 0.00000625 0.00267911]
 [0.00002033 0.00033776 0.00022622 0.00014722 0.99329245 0.00043497
  0.00437345 0.00019047 0.0005073  0.00047   ]
 [0.00050128 0.00064007 0.9017445  0.0429039  0.02239559 0.0008784
  0.02877389 0.00007327 0.00152967 0.00055942]
 [0.00000881 0.00001615 0.00000229 0.00002181 0.00442833 0.9948368
  0.00042632 0.00000282 0.00002981 0.00022678]
 [0.00002721 0.00002956 0.00004643 0.00004721 0.01746728 0.00027939
  0.00000672 0.00064141 0.00164838 0.9798063 ]
 [0.00000011 0.0002037  0.9805541  0.0133286  0.00034278 0.00000591
  0.00000145 0.00000916 0.0055396  0.

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.111451395.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-04-12-06:13:13
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-04-12-06:13:13
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.971, global_step = 20000, loss = 0.10002323
{'accuracy': 0.971, 'global_step': 20000, 'loss': 0.10002323}


SystemExit: 

/usr/local/lib/python3.5/dist-packages/IPython/core/interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
